# Dataset pre-processing
In this section we are loading our dataset for predictions, in this case we hace 3 datasets:

* Train
* Test
* Validation

So far, we are using just the train dataset. The first step is define the meaning of outfit, as we have describe previously, an oufit wil be define as:

**Men**

* Tshirt and Polos
* Pullover (optional)
* Shorts or pants or jeans 
* Shoes or sneakers 

**Women**
* Top
* Bottom
* Pullover (optional)
* Outerwear (optional)
* Shoes

In [2]:
# Libreries
import pandas as pd
import numpy as np

import json

In [ ]:
# Loading the dataset
train_path = '../Datasets/train_no_dup.json'
with open(train_path) as file:
  df_train = json.load(file)

# Showing

display(df_train[0])

{'name': 'Casual',
 'views': 8743,
 'items': [{'index': 1,
   'name': 'mock neck embroidery suede sweatshirt',
   'price': 24.0,
   'likes': 10,
   'image': 'http://img2.polyvoreimg.com/cgi/img-thing?.out=jpg&size=m&tid=194508109',
   'categoryid': 4495},
  {'index': 2,
   'name': 'luxe double zip hooded jacket',
   'price': 150.0,
   'likes': 2250,
   'image': 'http://img2.polyvoreimg.com/cgi/img-thing?.out=jpg&size=m&tid=188778349',
   'categoryid': 25},
  {'index': 3,
   'name': 'citizens humanity high rise rocket hem jean',
   'price': 248.0,
   'likes': 2437,
   'image': 'http://img1.polyvoreimg.com/cgi/img-thing?.out=jpg&size=m&tid=188977857',
   'categoryid': 27},
  {'index': 4,
   'name': 'suede tie short boots',
   'price': 37.0,
   'likes': 2,
   'image': 'http://img1.polyvoreimg.com/cgi/img-thing?.out=jpg&size=m&tid=194942557',
   'categoryid': 261},
  {'index': 5,
   'name': 'cloth travel school backpack',
   'price': 22.0,
   'likes': 2,
   'image': 'http://img2.polyvoreim

## Gender

It is neccesary to keep in mind the importance of divide the genders during the training, that is because the clothes are different so try to get an outfit combined the clothes designed for a male with cloths for a female, could be get bad recommendation due to the pattern. That's why is mandatory filter the womens clothes and then just keep the outfit that matches with out definition of outfit.

The principal problem about this is the lack description regarding the gender. That's why the filter by gender is just reduced a little bit for each gender.

Also, it is possible to use NLTK in order to get synonyms for females and males terms.

In [4]:
for i in range(2):
    display(df_train[i]['desc'])

'A fashion look from January 2017 by beebeely-look featuring Fuji, Citizens of Humanity, casual, casualoutfit, Packandgo, winterjacket and gearbest'

'A fashion look from April 2014 featuring destroyed shirt, skinny fit jeans and vans shoes. Browse and shop related looks.'

In [25]:
from nltk.corpus import wordnet
import nltk
import re
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import word_tokenize
# nltk.download('wordnet')
nltk.download('punkt_tab')


def get_synonyms(word):
    synonyms = []
    for syn in wordnet.synsets(word):
        for lemma in syn.lemmas():
            synonyms.append(lemma.name())
    return set(synonyms)


lemmatizer = WordNetLemmatizer()
def preprocess_description(description):
    description = description.lower()
    
    description = re.sub(r'[^a-zA-Z0-9\s]', '', description)
    
    tokens = word_tokenize(description)
    lemmatized_tokens = [lemmatizer.lemmatize(token) for token in tokens]
    
    return ' '.join(lemmatized_tokens)

female_synonyms = get_synonyms("woman") | get_synonyms("girl") | get_synonyms('dress')
print(female_synonyms)

[nltk_data] Downloading package punkt_tab to /home/fredin/nltk_data...


{'arrange', 'lady_friend', 'full-dress', 'woman', 'crop', 'little_girl', 'frock', 'primp', 'tog', 'dress_out', 'lop', 'decorate', 'adult_female', 'female_child', 'daughter', 'missy', 'plume', 'get_dressed', 'dress', 'wearing_apparel', 'clip', 'snip', 'coiffe', 'girl', 'raiment', 'charwoman', 'fair_sex', 'womanhood', 'garnish', 'miss', 'coif', 'habilitate', 'set', 'young_lady', 'cleaning_woman', 'fille', 'cleaning_lady', 'young_woman', 'garment', 'clothes', 'preen', 'do', 'garb', 'fit_out', 'clothe', 'dress_up', 'attire', 'groom', 'curry', 'cut_back', 'apparel', 'trim', 'prune', 'coiffure', 'girlfriend', 'enclothe', 'char', 'line_up'}


[nltk_data]   Unzipping tokenizers/punkt_tab.zip.


In [61]:
for index in range(len(df_train)):
    df_train[index]['desc'] = preprocess_description(df_train[index]['desc'])

In [89]:
# Filtering men's clothles
substrings_filter_men = ["men's", "Men", "man", 'Man', "men's fashion", "menswear look"]
men_fashion = filter(lambda x: any(substring in x['desc'] for substring in substrings_filter_men), df_train)
men_fashion = list(men_fashion)

# Filtering women's clothles
substrings_filter_woman = ["women", "woman", "womens", "girl", "girls", "womens fashion", "female","females", "top", "cute", "bag", "blouses", "skirts","skinny","bras","camisoles","bikini","coats","cocktail"]
plus_synonyms = ['arrange', 'lady friend', 'full dress', 'woman', 'crop', 'little girl', 'frock', 'primp', 'tog', 'dress out', 'lop', 'decorate', 'adult female', 'female child', 'daughter', 'missy', 'plume', 'get dressed', 'dress', 'wearing apparel', 'clip', 'snip', 'coiffe', 'girl', 'raiment', 'charwoman', 'fair sex', 'womanhood', 'garnish', 'miss', 'coif', 'habilitate', 'set', 'young_lady', 'cleaning woman', 'fille', 'cleaning lady', 'young woman', 'garment', 'clothes', 'preen', 'do', 'garb', 'fit out', 'clothe', 'dress_up', 'attire', 'groom', 'curry', 'cut back', 'apparel', 'trim', 'prune', 'coiffure', 'girlfriend', 'enclothe', 'char', 'line_up']
substrings_filter_woman.extend(plus_synonyms)
women_fashion = filter(lambda x: any(substring in x['desc'] for substring in substrings_filter_woman), df_train)
women_fashion = list(women_fashion)

# Number of women's outfits:
print(len(women_fashion))

# Number of men's oufits
print(len(men_fashion))

# The total of outfits
print(len(df_train))

7661
2644
17316


**Another approach to select the appropiate outfits**

We can select directly just the outfits that we want to keep, in this case these are outfits just for women. Rather than select just outfits related to women, we can select the outfits that correspond with the structure that we are look forward to train the model.

The next step is just keep the outfits that matches with our outfit definition, additional this help to tune the filter by gender. We can classify the categories of each outfit and reduce in general categories:

<details>    
<summary>
    <font size="3" color="pink"><b>Categorías que se mantuvieron</b></font>
</summary>
<p>

**Women**
* Dress
    * 3 Dresses
    * 4 Day Dresses
    * 5 Cocktail Dresses

* Top
    * 11 Tops
    * 15 Tunics
    * 17 Blouses
    * 21 T-Shirts
    * 104 Tank Tops
    * 244 Rompers
    * 245 Bras
    * 247 Camisoles
    * 252 Activewear Tops
    * 257 Sports Bras
    * 309 Activewear Tank Tops
    * 4517 Bikini Tops

* Bottom
    * 7 Skirts
    * 8 Mini Skirts
    * 9 Knee Length Skirts
    * 10 Long Skirts
    * 27 Jeans
    * 28 Pants
    * 29 Shorts
    * 237 Skinny Jeans
    * 238 Bootcut Jeans
    * 239 Wide Leg Jeans
    * 241 Leggings
    * 253 Activewear Pants
    * 254 Activewear Skirts
    * 255 Activewear Shorts
    * 4518 Bikini Bottoms

* Pullover (optional)
    * 19 Sweaters
    * 4495 Sweatshirts
    * 4496 Hoodies

* Outerwear (optional)
    * 18 Cardigans
    * 23 Outerwear
    * 24 Coats
    * 25 Jackets
    * 26 Vests
    * 236 Blazers
    * 256 Activewear Jackets

* Shoes
    * 41 Shoes
    * 49 Sneakers
    * 261 Ankle Booties
    * 262 Mid Calf Boots
    * 263 Knee High Boots
    * 264 Over-The-Knee Boots
    * 268 Athletic Shoes

* Belts (optional)
    * 52 Belts

</p>

In [ ]:
# Filtering outfits for women fashion
# Categories
numbers_list = [
    2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 15, 17, 18, 19, 21, 23, 24, 25, 26, 27, 28, 29, 
    41, 49, 52, 104, 236, 237, 238, 239, 241, 
    244, 245, 247, 252, 253, 254, 255, 256, 257, 261, 262, 263, 264, 309, 
    4517, 4518, 4241, 240, 241, 250, 251, 4495, 4496
]

category_numbers = [3, 23, 41, 7, 11, 27, 25]
womens_fashion = []

for outfit in df_train:
    outfit_categories = {item['categoryid'] for item in outfit['items']}
    if outfit_categories.issubset(numbers_list) and len(outfit_categories)>= 3:
        womens_fashion.append(outfit)

print(len(womens_fashion))
womens_fashion


142


[{'name': 'Cold Day with Niall',
  'views': 109,
  'items': [{'index': 1,
    'name': 'chicnova fashion pure color long sleeves sweater',
    'price': 33.0,
    'likes': 1814,
    'image': 'http://img1.polyvoreimg.com/cgi/img-thing?.out=jpg&size=m&tid=148184208',
    'categoryid': 19},
   {'index': 2,
    'name': 'black contrast pu leather tassel crop jacket',
    'price': 32.0,
    'likes': 9943,
    'image': 'http://img1.polyvoreimg.com/cgi/img-thing?.out=jpg&size=m&tid=143371816',
    'categoryid': 25},
   {'index': 3,
    'name': 'silk pants',
    'price': 185.0,
    'likes': 1929,
    'image': 'http://img1.polyvoreimg.com/cgi/img-thing?.out=jpg&size=m&tid=127512671',
    'categoryid': 28},
   {'index': 4,
    'name': 'topshop ace back buckle boots',
    'price': 93.0,
    'likes': 4666,
    'image': 'http://img2.polyvoreimg.com/cgi/img-thing?.out=jpg&size=m&tid=153812324',
    'categoryid': 261}],
  'image': 'http://ak2.polyvoreimg.com/cgi/img-set/cid/199683429/id/gEuwLhgo5hGVLjDh

Also, we can explore with the whole dataset and then get the recommendations.

In [92]:
women_fashion

[{'name': 'Being a Vans shoe model with Luke. Idk about this title',
  'views': 188,
  'items': [{'index': 1,
    'name': 'nirvana distressed t-shirt',
    'price': 10.0,
    'likes': 1290,
    'image': 'http://img2.polyvoreimg.com/cgi/img-thing?.out=jpg&size=m&tid=108042640',
    'categoryid': 21},
   {'index': 2,
    'name': 'rag bone rock w/ black skinny jeans',
    'price': 235.0,
    'likes': 17406,
    'image': 'http://img2.polyvoreimg.com/cgi/img-thing?.out=jpg&size=m&tid=103135174',
    'categoryid': 237},
   {'index': 3,
    'name': 'vans authentic black mono trainers',
    'price': 43.0,
    'likes': 10734,
    'image': 'http://img2.polyvoreimg.com/cgi/img-thing?.out=jpg&size=m&tid=107307153',
    'categoryid': 49},
   {'index': 4,
    'name': 'time low rubber bracelet hot topic',
    'price': 5.6,
    'likes': 373,
    'image': 'http://img2.polyvoreimg.com/cgi/img-thing?.out=jpg&size=m&tid=107349261',
    'categoryid': 106},
   {'index': 5,
    'name': 'veil logo rubber brac

### Creating the routes for each dataset

In [38]:
import os
import cv2

def buscar_directorio(nombre_directorio, ruta_carpeta):
    for root, dirs, files in os.walk(ruta_carpeta):
        if nombre_directorio in dirs:
            ruta_completa = os.path.join(root, nombre_directorio)
            print("Ruta completa:", ruta_completa)
            return ruta_completa

def buscar_directorio(nombre_directorio, ruta_carpeta):
    for root, dirs, files in os.walk(ruta_carpeta):
        if nombre_directorio in dirs:
            ruta_completa = os.path.join(root, nombre_directorio)
            return ruta_completa

In [93]:
route = "../Images"

# Dataset limited
for i in range(len(womens_fashion)):
    id_outfit = womens_fashion[i]['set_id']
    dir_searched = str(id_outfit)
    route_relative = buscar_directorio(dir_searched, route)
    for j in range(len(womens_fashion[i]['items'])):
        number = womens_fashion[i]['items'][j]['index']
        route_complete = str(route_relative).replace("\\","/")+'/'+str(number)+'.jpg'
        # Substitution
        womens_fashion[i]['items'][j]['image'] = route_complete

# Whole dataset
for i in range(len(women_fashion)):
    id_outfit = women_fashion[i]['set_id']
    dir_searched = str(id_outfit)
    route_relative = buscar_directorio(dir_searched, route)
    for j in range(len(women_fashion[i]['items'])):
        number = women_fashion[i]['items'][j]['index']
        route_complete = str(route_relative).replace("\\","/")+'/'+str(number)+'.jpg'
        # Substitution
        women_fashion[i]['items'][j]['image'] = route_complete

In [48]:
women_fashion

[{'name': 'Boho (39)',
  'views': 62,
  'items': [{'index': 1,
    'name': 'yoins leather sexy v-neck sleeveless crop top',
    'price': 16.0,
    'likes': 6637,
    'image': '../Images/206969379/1.jpg',
    'categoryid': 11},
   {'index': 2,
    'name': 'solid color long sleeve irregular blazer',
    'price': 99.0,
    'likes': 24,
    'image': '../Images/206969379/2.jpg',
    'categoryid': 236},
   {'index': 3,
    'name': 'alice+olivia floral pattern a-line skirt',
    'price': 295.0,
    'likes': 338,
    'image': '../Images/206969379/3.jpg',
    'categoryid': 9},
   {'index': 4,
    'name': 'zipped top chunky booties',
    'price': 32.0,
    'likes': 1503,
    'image': '../Images/206969379/4.jpg',
    'categoryid': 261},
   {'index': 5,
    'name': 'gold boho turquoise leaf tassel earrings',
    'price': 7.99,
    'likes': 3449,
    'image': '../Images/206969379/5.jpg',
    'categoryid': 64},
   {'index': 6,
    'name': 'etro heart locket necklace',
    'price': 175.0,
    'likes'

### Saving the json

In [94]:
output_file_1 = "../Datasets/womens_fashion_defined.json"
output_file_2 = "../Datasets/womens_fashion_wholeDataSet.json"

with open(output_file_1, "w") as outfile:
    json.dump(womens_fashion, outfile)

print("Json Saved!:", output_file_1)

Json Saved!: ../Datasets/womens_fashion_defined.json


In [95]:
with open(output_file_2, "w") as outfile:
    json.dump(women_fashion, outfile)
print("Json Saved!:", output_file_2)

Json Saved!: ../Datasets/womens_fashion_wholeDataSet.json


At the end of the day, we can consider the both dataset, but the problem is cover the all categories. So, just for terms of simplicity, am going to work with the dataset limited.